In [18]:
import sys
import os
import logging
import logging.config
import json
import shutil
import matplotlib as mpl
import matplotlib.pyplot as plt
import pickle as pkl

# mpl.use('Agg')

import numpy as np

import copy
import sqlite3
import git
import torch
import torchvision
import torch.autograd as autograd
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

from misc.database import Database

from prediction_model import utils
from prediction_model.models.lstm_l0 import L0SeqLSTM
from prediction_model.models.fully_connected_l0 import L0FCN
from prediction_model.models.ntm_aio_l0 import EncapsulatedNTML0
from prediction_model.models.ntm_aio import EncapsulatedNTM
from prediction_model.objectives.sse import SSE
from prediction_model.objectives.logistic_loss import LogisticLoss

# plotting tools
from bokeh.io import output_notebook, show
from bokeh.layouts import gridplot
from bokeh.plotting import figure
from bokeh.models import CustomJS, Slider, ColumnDataSource, Whisker, Range1d

from datetime import datetime
from types import SimpleNamespace

output_notebook()

Loading BokehJS ...

In [6]:
def model_forward_fcn(X_train, y_train, model_p, objective_p, optimizer_p, l0_reg, backward=True, enable_gpu=False):
    model_out = []
    total_log_loss = None
    total_penalty = None
    
    X_train = torch.FloatTensor(X_train)
    y_train = torch.FloatTensor(y_train)
    if enable_gpu:
        X_train = X_train.cuda()
        y_train = y_train.cuda()

    out, (hidden, penalty) = model_p.forward(X_train)
#         ht, ct = hidden
    # print(x_t1, out)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    # print(out)

#     print(out.shape)
#     print(y_train.shape)
    log_loss = objective_p(out, y_train)

    if total_log_loss is None:
        total_log_loss = log_loss
        total_penalty = penalty
    else:
        total_log_loss += log_loss
        total_penalty += penalty

    model_out.append(out.cpu().data.numpy())

    total_loss = total_log_loss + l0_reg * total_penalty

    if backward:
        model.zero_grad()
        total_loss.backward()
        optimizer_p.step()

    if backward:
        total_penalty = np.sum(total_penalty.cpu().data.numpy())

    return model, \
           (np.sum(total_log_loss.cpu().data.numpy()), total_penalty), \
           model_out

In [7]:
def logistic_map(x, alpha):
    return alpha*x*(1-x)

def linear_map(x, alpha):
    return alpha*x

In [ ]:
seed = 0
alpha = 3.3
enable_gpu = True
l0_reg = 0.001

# for seed in range(args.n_seeds):
utils.common.set_global_seeds(seed)

model = L0FCN(input_bins=1,
              output_bins=1,
              fc_config=[20]*2,
              enable_gpu=True,
              test_mode=False)

if enable_gpu:
    model = model.cuda()

optimizer = optim.Adam(model.parameters(),
                       lr=1e-4,
                       weight_decay=0)

objective = SSE()

prev_loss = 0
epoch = 0
best_model = None
best_acc = 100
best_nparams = 0

while True:
    X_train = np.random.rand(50)
    y_train = np.array(list(map(lambda x: logistic_map(x, alpha), X_train)))

    X_train = X_train.reshape((-1, 1))
    y_train = y_train.reshape((-1, 1))

    model.train()
    model, (log_loss, penalty), model_out = model_forward_fcn(X_train,
                                                              y_train,
                                                              model,
                                                              objective,
                                                              optimizer,
                                                              l0_reg,
                                                              enable_gpu=enable_gpu)
    total_loss = (log_loss + l0_reg * penalty)

    # Validation
    model.eval()

    _, _, model_out = model_forward_fcn(X_train,
                                        y_train,
                                        model,
                                        objective,
                                        optimizer,
                                        l0_reg,
                                        enable_gpu=enable_gpu,
                                        backward=False)
#     predictions = (np.array(model_out) > 0.5).astype(int)
    predictions = np.array(model_out).flatten()
    actual = y_train.flatten()
    # print(actual == predictions)
    accuracy = np.sum(actual == predictions) / len(actual)
    model_nparams = model.get_l0_norm()

    # if accuracy > best_acc or (accuracy == best_acc and best_nparams > model_nparams):
    if log_loss <= best_acc and not (np.isnan(log_loss) or np.isnan(penalty)):
        best_model = copy.deepcopy(model.state_dict())
        best_acc = log_loss
        best_nparams = model_nparams
    div = X_train.shape[0]
    # print diagnostics
    if epoch % 100 == 0:
        model_out = np.array(model_out).flatten()
        print("")
        print("epoch: {} SSE loss: {}, l0 penalty: {} total loss: {}".format(epoch,
                                                                              log_loss / div,
                                                                              penalty / div,
                                                                              total_loss))
        print("accuracy: {}, actual: {}, predicted: {}, n_params: {} model_out: {}".format(accuracy,
                                                                                                 X_train.flatten(),
                                                                                                 predictions,
                                                                                                 model.get_l0_norm(),
                                                                                                 model_out))

    if np.abs(total_loss - prev_loss) <= 1e-9:
        print("Training converged: {}".format(np.abs(total_loss - prev_loss)))
        break

    prev_loss = total_loss
    epoch += 1

    if np.isnan(log_loss) or np.isnan(penalty):
        print("NaN detected")
        break
#     break

fc0
Gate mode: unique
fc1
Gate mode: unique
Gate mode: unique

epoch: 0 SSE loss: 0.07172363758087158, l0 penalty: 8.002297973632812 total loss: 3.9862967777252196
accuracy: 0.0, actual: [0.5488135  0.71518937 0.60276338 0.54488318 0.4236548  0.64589411
 0.43758721 0.891773   0.96366276 0.38344152 0.79172504 0.52889492
 0.56804456 0.92559664 0.07103606 0.0871293  0.0202184  0.83261985
 0.77815675 0.87001215 0.97861834 0.79915856 0.46147936 0.78052918
 0.11827443 0.63992102 0.14335329 0.94466892 0.52184832 0.41466194
 0.26455561 0.77423369 0.45615033 0.56843395 0.0187898  0.6176355
 0.61209572 0.616934   0.94374808 0.6818203  0.3595079  0.43703195
 0.6976312  0.06022547 0.66676672 0.67063787 0.21038256 0.1289263
 0.31542835 0.36371077], predicted: [0.4911132  0.49064255 0.49093026 0.49112654 0.4914679  0.49078408
 0.4914314  0.49030647 0.4901696  0.4915772  0.49049687 0.4911807
 0.49104798 0.4902421  0.4924263  0.4923826  0.49256444 0.49041906
 0.49052274 0.4903479  0.4901427  0.4904827


epoch: 500 SSE loss: 0.0602869987487793, l0 penalty: 7.961536865234375 total loss: 3.4124267807006836
accuracy: 0.0, actual: [0.8812033  0.53122103 0.8680575  0.77755907 0.96932112 0.92571412
 0.16927561 0.57996402 0.02856338 0.68828411 0.54150551 0.14278145
 0.66640611 0.36708941 0.09459162 0.00299151 0.60631975 0.79011012
 0.47399445 0.36391856 0.75603037 0.0063267  0.80624946 0.14631303
 0.2934198  0.61383733 0.8059898  0.14708033 0.66029159 0.40847581
 0.25638414 0.39374154 0.38463804 0.83570583 0.53699062 0.84165466
 0.16601442 0.83759583 0.3109018  0.71662891 0.49894272 0.59874476
 0.64255778 0.64013713 0.93336891 0.68057536 0.57611589 0.27045168
 0.83392349 0.2913378 ], predicted: [0.50283116 0.50338775 0.5028457  0.5029458  0.5027587  0.50279295
 0.5041703  0.50326824 0.5044624  0.50304455 0.5033616  0.5042253
 0.503086   0.5037596  0.50432533 0.50451547 0.5032099  0.50293195
 0.50353324 0.5037662  0.5029696  0.50450855 0.5029141  0.5042179
 0.50391257 0.5031932  0.50291437 0.


epoch: 1000 SSE loss: 0.07380448341369629, l0 penalty: 7.922037963867187 total loss: 4.086326068878174
accuracy: 0.0, actual: [0.30764535 0.06200521 0.98878508 0.7190903  0.75756964 0.26375811
 0.81423212 0.56902059 0.45944772 0.13070624 0.31822656 0.3471398
 0.04941394 0.96384525 0.96475062 0.1106671  0.33928814 0.56340746
 0.48681865 0.56492329 0.86105383 0.81537125 0.41010138 0.52310581
 0.18856046 0.45604781 0.76245352 0.25340822 0.24580262 0.99679214
 0.22599421 0.962532   0.24860247 0.71298981 0.04488238 0.67372927
 0.41643382 0.51367789 0.51061752 0.37990148 0.01794764 0.80771941
 0.41246825 0.28481926 0.89542746 0.51598704 0.98335094 0.4560161
 0.71131126 0.09003222], predicted: [0.5180641  0.51786816 0.5182002  0.51817214 0.518176   0.5180318
 0.5181818  0.51815104 0.518135   0.51793367 0.5180719  0.5180932
 0.51785266 0.51819706 0.5181971  0.5179189  0.51808745 0.5181502
 0.518139   0.51815045 0.51818657 0.5181819  0.5181278  0.5181443
 0.51797634 0.51813453 0.51817656 0.518


epoch: 1500 SSE loss: 0.07106655597686767, l0 penalty: 7.881582641601563 total loss: 3.947406930923462
accuracy: 0.0, actual: [0.24392333 0.65495435 0.35150695 0.62498055 0.03401694 0.24540688
 0.22322093 0.0760436  0.83643934 0.88957214 0.18126889 0.78185092
 0.59343407 0.1847256  0.37908656 0.9475536  0.01381148 0.47050336
 0.78318807 0.62917569 0.36378382 0.02195515 0.8975815  0.50285664
 0.29962934 0.04863477 0.9932151  0.81687624 0.16885527 0.88573366
 0.06075629 0.8205812  0.25389633 0.99687541 0.04379909 0.15060614
 0.78009182 0.02238677 0.13359511 0.23338146 0.22705116 0.39122358
 0.77979902 0.18917251 0.32549157 0.44852835 0.3491879  0.64779936
 0.98710881 0.02330982], predicted: [0.5306613  0.53152645 0.53088915 0.53146833 0.5302167  0.53066444
 0.5306174  0.5303057  0.5317547  0.53181785 0.53052855 0.53168976
 0.5314015  0.53053594 0.53094757 0.5318868  0.53017384 0.53114116
 0.5316914  0.5314772  0.53091514 0.5301911  0.5318274  0.5312097
 0.5307793  0.5302476  0.53194106 


epoch: 2000 SSE loss: 0.06629046440124511, l0 penalty: 7.83825927734375 total loss: 3.7064361839294433
accuracy: 0.0, actual: [0.53525707 0.90404425 0.50239657 0.10087001 0.52758198 0.71122893
 0.31295428 0.05032535 0.12328206 0.77969075 0.94802187 0.71818603
 0.75389358 0.10964897 0.63814993 0.28945067 0.361702   0.00315978
 0.04352426 0.79419409 0.77746827 0.56411938 0.38736774 0.34514564
 0.41004102 0.06705749 0.97356847 0.06405922 0.10844153 0.47859636
 0.87148378 0.98030973 0.67780738 0.87716066 0.26757641 0.61586974
 0.44980164 0.61761576 0.80281463 0.03813337 0.29641567 0.33406014
 0.50907489 0.74504766 0.59307464 0.34360118 0.30266013 0.27967976
 0.92107048 0.87532113], predicted: [0.53909355 0.5400574  0.5389996  0.53785104 0.5390716  0.53959674
 0.53845775 0.5377065  0.53791517 0.5397678  0.5401552  0.53961426
 0.5397034  0.5378762  0.53938776 0.5383905  0.53859717 0.53757155
 0.537687   0.539804   0.53976226 0.53917605 0.5386706  0.5385498
 0.53873545 0.5377543  0.540212   

...


epoch: 230400 SSE loss: 0.002654775679111481, l0 penalty: 3.3727261352539064 total loss: 0.30137509071826935
accuracy: 0.0, actual: [0.99728983 0.76265098 0.92926665 0.37391042 0.87015491 0.68007582
 0.01437554 0.73207548 0.77475692 0.1055234  0.16409874 0.64355988
 0.32977963 0.25627853 0.22199332 0.04836303 0.03646369 0.46345915
 0.4201196  0.95699902 0.81568498 0.32799626 0.85306163 0.77119859
 0.42181969 0.79874662 0.4041556  0.50460552 0.47016696 0.35541417
 0.01556701 0.64416309 0.65293775 0.45148337 0.05877034 0.22316157
 0.8806193  0.66994968 0.0243992  0.39066072 0.09684827 0.14563832
 0.0760096  0.40930246 0.46382281 0.86281281 0.11457634 0.68116073
 0.87776642 0.11754702], predicted: [0.12241004 0.61187875 0.18046175 0.84101576 0.28575522 0.7935695
 0.07896081 0.7001055  0.5743883  0.26497012 0.46118203 0.82734525
 0.8053477  0.6225002  0.55289125 0.1272211  0.1077195  0.84038484
 0.8406904  0.15211114 0.44380572 0.8012255  0.33056292 0.5855179
 0.84067845 0.49793857 0.8408


epoch: 230900 SSE loss: 0.0023542359471321107, l0 penalty: 3.370191650390625 total loss: 0.28622137987613677
accuracy: 0.0, actual: [0.29889891 0.87652256 0.46373656 0.87066804 0.39148863 0.12528395
 0.55524728 0.50920526 0.61754601 0.81997497 0.96713104 0.33073511
 0.2343198  0.10529734 0.38476461 0.11268881 0.43620355 0.54183588
 0.00656948 0.60496255 0.27586963 0.1473471  0.59084001 0.72494686
 0.77317343 0.93732915 0.0970717  0.81127382 0.77458167 0.16459599
 0.15906865 0.21027757 0.90241085 0.3473072  0.46650533 0.2309894
 0.88789323 0.98214799 0.25555292 0.17134784 0.51585582 0.71450594
 0.67254811 0.36540602 0.45422918 0.82369744 0.20396276 0.57756259
 0.31963812 0.92435348], predicted: [0.7171964  0.26441592 0.84001213 0.27805576 0.84051317 0.3264022
 0.83937573 0.8396962  0.8360382  0.42218313 0.1422909  0.8016253
 0.5788759  0.26083526 0.8405597  0.28407222 0.8402033  0.83946913
 0.07173663 0.8389434  0.6623894  0.40747216 0.83912766 0.7129998
 0.5717302  0.1682732  0.236466


epoch: 231400 SSE loss: 0.015805469751358034, l0 penalty: 3.3677813720703127 total loss: 0.9586625561714173
accuracy: 0.0, actual: [0.30727671 0.54652719 0.39463957 0.22095991 0.00194602 0.09435486
 0.32254192 0.23712423 0.08088216 0.28330608 0.14782545 0.18775998
 0.91961387 0.52729268 0.45228493 0.55804897 0.36572595 0.80125826
 0.85509059 0.5441791  0.10804435 0.91335951 0.3510032  0.84595524
 0.54178034 0.97948149 0.04963399 0.44866149 0.58213705 0.51124176
 0.3174517  0.80943194 0.28763401 0.78660771 0.53841284 0.86231508
 0.17975654 0.90917723 0.40124287 0.76749369 0.37908623 0.51241115
 0.05695043 0.5222208  0.03847594 0.5874883  0.74698999 0.54463188
 0.31219325 0.01905894], predicted: [0.73727924 0.8384386  0.83947396 0.54824376 0.06760265 0.22599654
 0.7781804  0.58395696 0.19076757 0.6774249  0.40568385 0.50865245
 0.18599586 0.83857    0.83908165 0.8383598  0.8396704  0.4714055
 0.30961946 0.83845466 0.26626804 0.19414827 0.83977044 0.3339759
 0.838471   0.131488   0.12550


epoch: 231900 SSE loss: 0.0025533291697502135, l0 penalty: 3.364961853027344 total loss: 0.2959145511388779
accuracy: 0.0, actual: [0.78380962 0.06217624 0.55486815 0.55926402 0.04454844 0.77510779
 0.63221405 0.43478325 0.70979448 0.69767746 0.35195221 0.06392629
 0.19706111 0.34795254 0.64531583 0.37609535 0.80091979 0.35422367
 0.25897053 0.3171383  0.43666662 0.11902356 0.97017439 0.2856096
 0.63648903 0.99725314 0.03810153 0.80720166 0.20026573 0.25398337
 0.86896157 0.77426662 0.44461645 0.93385985 0.28148229 0.87977734
 0.92730378 0.8659586  0.51665596 0.18810586 0.82704963 0.95026379
 0.08124502 0.09324921 0.17576861 0.73035011 0.0589639  0.67684717
 0.50602176 0.26426123], predicted: [0.5329074  0.15035251 0.8379301  0.8379008  0.11797084 0.5606921
 0.8295141  0.8387303  0.746596   0.76359516 0.8392804  0.15393752
 0.5155123  0.8350739  0.8220175  0.83912027 0.4778396  0.83926535
 0.62059575 0.7634222  0.8387178  0.30384773 0.13829875 0.682164
 0.82753366 0.11924084 0.1077270


epoch: 232400 SSE loss: 0.0021257321536540985, l0 penalty: 3.362425537109375 total loss: 0.27440788453817366
accuracy: 0.0, actual: [7.03684382e-01 4.97574123e-01 3.63691230e-04 5.19822896e-02
 2.79901547e-01 6.36622941e-01 3.39989596e-01 9.45505248e-01
 6.91200032e-01 4.81180553e-01 2.18639988e-01 5.31942483e-02
 5.32051644e-01 6.40673053e-01 4.89966884e-01 4.52114266e-01
 2.57516210e-01 8.19118468e-01 5.52686776e-01 8.72209212e-01
 6.00186135e-01 1.69077258e-01 3.69191688e-01 9.99788420e-01
 4.89166174e-01 7.59378305e-01 2.10255812e-02 6.58632384e-01
 7.29831086e-01 9.23814415e-01 1.49441297e-01 7.56345847e-01
 9.49115614e-01 4.36274099e-01 2.67570061e-01 5.43492046e-03
 3.00417648e-01 5.11433799e-01 3.58248750e-01 8.66818010e-01
 7.25078706e-01 1.66943370e-01 1.61090294e-01 2.20227487e-02
 1.89594399e-01 5.43087944e-02 9.05618737e-01 3.31105200e-01
 7.92365812e-01 8.23853109e-02], predicted: [0.75893646 0.838903   0.06622783 0.12874234 0.6661897  0.8290867
 0.8163064  0.1597435  0.

In [15]:
model_test = L0FCN(input_bins=1,
                  output_bins=1,
                  fc_config=[20]*2,
                  enable_gpu=True,
                  test_mode=False)
model_test.load_state_dict(best_model)

fc0
Gate mode: unique
fc1
Gate mode: unique
Gate mode: unique


<All keys matched successfully>

In [16]:
model_test.get_l0_norm()

tensor(57)

In [17]:
model_test = model_test.cuda()
model_test.eval()

x = np.arange(0, 1, 0.01)
y = list(map(lambda val: logistic_map(val, alpha), x))
y_pred = None
k = 1
for i in range(k):
    y_pred_k = []
    for x_val in x:
        x_val = torch.FloatTensor([x_val]).cuda()
        out, _ = model_test.forward(x_val)
        out = torch.clamp(out, -8, 8)
        out = F.sigmoid(out)
        y_pred_k.append(out.data.cpu().numpy()[0])
    
    if y_pred is None:
        y_pred = np.array(y_pred_k)
    else:
        y_pred += np.array(y_pred_k)

y_pred = y_pred/k
plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,wheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(x,
          y)
plot.line(x,
          y_pred,
         line_color="orange")
plot.x(X_train.flatten(),
       y_train.flatten())

plot.xaxis.axis_label = 'x'
plot.yaxis.axis_label = 'f(x)'

show(plot)

In [19]:
series_pred = []
series_pred_in = []
series_actual = []
lambda_series_pred = []
lambda_series_actual = []
x_t_m = 0.7
x_t_a = x_t_m
x_t_i = x_t_m
n_points = 500

step = 0
tot_steps = 5

for i in range(n_points):
    x_val = torch.FloatTensor([x_t_m]).cuda()
    out, _ = model_test.forward(x_val)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    lambda_series_pred.append(out.data.cpu().numpy()[0]/(x_t_m*(1-x_t_m)))
    x_t_m = out.data.cpu().numpy()[0]
    series_pred.append(x_t_m)
    
    if step >= tot_steps:
        x_t_i = x_t_a
        step = 0
    
    x_val = torch.FloatTensor([x_t_i]).cuda()
    out, _ = model_test.forward(x_val)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    x_t_i = out.data.cpu().numpy()[0]
    series_pred_in.append(x_t_i)
    step += 1
    
    lambda_series_actual.append(logistic_map(x_t_a, alpha=alpha)/(x_t_a*(1-x_t_a)))
    x_t_a = logistic_map(x_t_a, alpha=alpha)
    series_actual.append(x_t_a)

plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,xwheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(range(n_points),
          series_actual)
plot.line(range(n_points),
          series_pred,
          line_color="orange")
plot.line(range(n_points),
          series_pred_in,
          line_color="red")

plot.xaxis.axis_label = 'step'
plot.yaxis.axis_label = 'f(x)'

show(plot)

mean_lambda_pred = [ np.mean(lambda_series_pred[:i]) 
                    for i in range(1, len(lambda_series_pred)) ]

plot = figure(**plot_options)
plot.line(range(n_points),
          lambda_series_actual)
plot.line(range(n_points),
          lambda_series_pred,
          line_color="orange")
plot.line(range(n_points),
          mean_lambda_pred,
          line_color="red")

plot.xaxis.axis_label = 'step'
plot.yaxis.axis_label = 'lambda'

show(plot)

In [20]:
n_points = 500

step = 0
tot_steps = 10
step_stderr = []

for step in range(1, tot_steps):
    print(step)
    step_err = []
    for i in range(n_points):  
        x_t_m = series_actual[i]
        err = []
        for pred_step in range(step):
            x_val = torch.FloatTensor([x_t_m]).cuda()
            out, _ = model_test.forward(x_val)
            out = torch.clamp(out, -8, 8)
            out = F.sigmoid(out)
            lambda_series_pred.append(out.data.cpu().numpy()[0]/(x_t_m*(1-x_t_m)))
            x_t_m = out.data.cpu().numpy()[0]
            
            try:
                err.append(np.abs(series_actual[i+pred_step+1] - x_t_m))
            except IndexError:
                break
        step_err.append(np.mean(err))
    step_err = np.array(step_err)
    step_err = step_err[~np.isnan(step_err)]
    step_stderr.append(np.mean(np.array(step_err)))
#     print(step_err)
#     print(step_stderr)
            
plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,xwheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(range(tot_steps),
          step_stderr,
         line_width=2)

plot.xaxis.axis_label = 'prediction steps'
plot.yaxis.axis_label = 'standard_error'

show(plot)

1
2
3
4
5
6
7
8
9


In [ ]:
step_stderr